In [5]:
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import os
import sys
import json
import time
from shapely.geometry import box,LineString,Point,MultiPoint,MultiLineString,MultiPolygon,Polygon
from shapely.ops import unary_union
import socket
current_dir = os.path.join(os.getcwd()) 
mother_path = os.path.abspath(os.path.join(current_dir, os.pardir))
print('mother_path:', mother_path)
sys.path.append(os.path.join(mother_path, 'PreProcessing'))
sys.path.append(os.path.join(mother_path))
from FittingProcedures import *
from plot import *
from Potential import *
from Grid import *
from PreprocessingObj import *
from ODfromfma import *
import time
from GeometrySphere import *
#import rustworkx as rw
import ast
try:
    import swifter
    from swifter import set_defaults
    import_swifter = True
    set_defaults(
    npartitions=None,
    dask_threshold=1,
    scheduler="processes",
    progress_bar=True,
    progress_bar_desc=None,
    allow_dask_on_strings=False,
    force_parallel=False)

except:
    pass
## BASIC PARAMS
plt.rcParams.update({
    "text.usetex": False,
})

if socket.gethostname()=='artemis.ist.berkeley.edu':
    TRAFFIC_DIR = '/home/alberto/LPSim/traffic_phase_transition'
else:
    TRAFFIC_DIR = os.getenv('TRAFFIC_DIR')
name = 'BOS'
grid_size = 0.02
hexagon_resolution = 8
dir_grid = os.path.join(TRAFFIC_DIR,'data','carto',name,'grid',str(grid_size))

## BASIC NEEDED OBJECTS
SFO_obj = GeometricalSettingsSpatialPartition(name,TRAFFIC_DIR)
bbox = SFO_obj.bounding_box
minx, miny, maxx, maxy = bbox
dir_geometries = os.path.join(TRAFFIC_DIR,'data','carto','{0}'.format(name))
grid = GetGrid(grid_size,SFO_obj.bounding_box,'EPSG:4326',dir_geometries)
df_distance,FoundDistMat = GetDirectionMatrix(dir_geometries,grid_size)
Tij = GetODGrid(dir_geometries,str(grid_size))
lattice = nx.read_graphml(os.path.join(dir_grid,"centroid_lattice.graphml"))
#VectorField = pd.read_csv('/home/alberto/LPSim/traffic_phase_transition/data/carto/BOS/grid/0.02/VectorField.csv')
#Potential = pd.read_csv('/home/alberto/LPSim/traffic_phase_transition/data/carto/BOS/grid/0.02/PotentialDataFrame.csv')

# GET POTENTIAL AND VECTOR FIELD
VectorField = GetVectorField(Tij,df_distance)
VectorFieldDir = os.path.join(TRAFFIC_DIR,'data','carto',name,'grid',str(grid_size))
lattice = GetPotentialLattice(lattice,VectorField)
lattice = SmoothPotential(lattice)
PotentialDataframe = ConvertLattice2PotentialDataframe(lattice)
PotentialDataframe = CompletePotentialDataFrame(VectorField,grid,PotentialDataframe)




mother_path: /home/aamad/Desktop/phd/berkeley/traffic_phase_transition/scripts
Initialize Grid: 0.02
ALREADY COMPUTED


# Compute Boundaries

In [7]:
boundary = gpd.overlay(SFO_obj.gdf_polygons, SFO_obj.gdf_polygons, how='union',keep_geom_type=False).unary_union
# CREATE BOUNDARY LINE
if isinstance(boundary, Polygon):
    boundary_line = LineString(boundary.exterior.coords)
elif isinstance(boundary, MultiPolygon):
    exterior_coords = []
    for polygon in boundary.geoms:
        exterior_coords.extend(polygon.exterior.coords)
    boundary_line = LineString(exterior_coords)

grid['position'] = grid.geometry.apply(lambda x: 'inside' if x.within(boundary) else ('edge' if x.touches(boundary) else 'outside'))
grid['relation_to_line'] = grid.geometry.apply(lambda poly: 'edge' if boundary_line.crosses(poly) else 'not_edge')

# COMPUTE PI

In [ ]:
from tqdm import tqdm
SumPot = np.sum(PotentialDataframe['V_out']) 
NumGridEdge = grid[grid['relation_to_line']=='edge'].shape[0]

def GetIndexEdgePolygon(grid):
    IndexEdge = []
    for i in range(grid.shape[0]):
        if grid.iloc[i]['relation_to_line']=='edge':
            IndexEdge.append(i)
    return IndexEdge

def PrepareJitCompiledComputeV(df_distance,IndexEdge,SumPot,NumGridEdge,PotentialDataframe,case = 'Vmax'):
    '''
        This function prepares the data for the jit compiled function ComputeV
    '''
    if case == 'Vmax':
        maski = [i in IndexEdge for i in df_distance['i']]
        dd = df_distance.loc[maski]
        maskj = [j in IndexEdge for j in dd['j']]
        dd = dd.loc[maskj]        
        result_vector = np.ones(len(dd))*SumPot/NumGridEdge
    else:
        maski = [i in IndexEdge for i in df_distance['i']]
        dd = df_distance.loc[maski]
        maskj = [j in IndexEdge for j in dd['j']]
        dd = dd.loc[maskj]
        PD = PotentialDataframe.loc[PotentialDataframe['index'].isin(IndexEdge)]
        result_vector = []
        for _, value in enumerate(PD['V_out'].values):
            result_vector.extend([value] * (len(PD)))

    return dd['distance'].to_numpy(dtype = np.float32),np.array(result_vector).astype(np.float32)
@numba.jit(parallel = True)
def ComputeJitV(distance_vector,potential_vector):
    if len(distance_vector) != len(potential_vector):
        print('distance_vector:',len(distance_vector))
        print('potential_vector:',len(potential_vector))
        raise ValueError('distance_vector and potential_vector must have the same length')
    return np.sum(distance_vector*potential_vector)    

def ComputePI(V,MaxV):
    return 1 - V/MaxV
distance_vector,potential_vector = PrepareJitCompiledComputeV(df_distance,GetIndexEdgePolygon(grid),SumPot,NumGridEdge,PotentialDataframe,case = 'Vmax')
Vmax = ComputeJitV(distance_vector,potential_vector)
distance_vector,potential_vector = PrepareJitCompiledComputeV(df_distance,GetIndexEdgePolygon(grid),SumPot,NumGridEdge,PotentialDataframe,case = 'V')
V = ComputeJitV(distance_vector,potential_vector)
ComputePI(V,MaxV)


In [24]:
1 - V/Vmax

0.8550464358285889

In [18]:


print(result_vector)

[13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426, 13500.486842557426,

In [19]:
len(result_vector)

385641